In [21]:
import wandb
import sys
import matplotlib.pyplot as plt
import scprep
import pandas as pd
sys.path.append('../../src/')
from train import load_data
# from diffusion import DiffusionModel
# from evaluate import get_results
from omegaconf import OmegaConf
# from main import load_data, make_model
import numpy as np
import os
import glob
import matplotlib.animation as animation
from matplotlib.animation import PillowWriter
import torch
from model2 import Autoencoder, Preprocessor, NoisePredictor
import magic
import torch
import pathlib
import copy
import plotly.graph_objects as go



In [22]:
import wandb
import sys
import matplotlib.pyplot as plt
import scprep
import pandas as pd
from omegaconf import OmegaConf
import os
import glob
import numpy as np
import torch
from torch import nn
import torch.optim as optim
from geodesic import jacobian, velocity, CondCurve, GeodesicBridge
from plotly3d.plot import scatter, trajectories
import torch
from torch import nn
import pytorch_lightning as pl
from procrustes import Procrustes
from torch.utils.data import DataLoader, TensorDataset

In [23]:
wandb.login()
api = wandb.Api()

In [24]:
entity = "xingzhis"
project = "dmae"
sweep_id = 'y7oimgga'
sweep = api.sweep(f"{entity}/{project}/{sweep_id}")
# Initialize an empty list to store run data
runs_data = []

# Iterate through each run in the sweep
for run in sweep.runs:
    # Extract metrics and configs
    metrics = run.summary._json_dict
    configs = run.config
    
    # Combine metrics and configs, and add run ID
    combined_data = {**metrics, **configs, "run_id": run.id}
    
    # Append the combined data to the list
    runs_data.append(combined_data)

# Create a DataFrame from the runs data
df = pd.DataFrame(runs_data)

In [25]:
data_name = 'hemisphere_ae'
run_ids = df[(df['data.name'] == data_name) & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/dimensions/latent'] == 2)][['run_id']]
assert len(run_ids) == 1
run_id = run_ids.iloc[0]
run = api.run(f"{entity}/{project}/{run_ids.iloc[0].values[0]}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
savefolder = None
plot_x = True
plot_recon = True
# title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
title = ''
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, s=2, alpha=0.2, title=title, filename=filename).show()
if plot_x:
    title1 = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(x, s=2, alpha=0.2, title=title1, filename=filename).show()
if plot_recon:
    title = f'[RECON] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(xh, s=2, alpha=0.2, title=title1, filename=filename).show()

/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/utilities/parsing.py:269: UserWarning:

Attribute 'preprocessor' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['preprocessor'])`.



In [26]:
entity = "xingzhis"
project = "dmae"
# sweep_id = 'svuepkxz'
sweep_id = 'y3scw04f'
sweep = api.sweep(f"{entity}/{project}/{sweep_id}")
# Initialize an empty list to store run data
runs_data = []

# Iterate through each run in the sweep
for run in sweep.runs:
    # Extract metrics and configs
    metrics = run.summary._json_dict
    configs = run.config
    
    # Combine metrics and configs, and add run ID
    combined_data = {**metrics, **configs, "run_id": run.id}
    
    # Append the combined data to the list
    runs_data.append(combined_data)

# Create a DataFrame from the runs data
df = pd.DataFrame(runs_data)
data_name = 'hemisphere_gaussian'
run_ids = df[(df['data.name'] == data_name)][['run_id']]
assert len(run_ids) == 1
run_id = run_ids.iloc[0]
run = api.run(f"{entity}/{project}/{run_ids.iloc[0].values[0]}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
noise_predictor = NoisePredictor.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    noise_predictor.eval()
    x_disc = torch.tensor(data['data'], dtype=torch.float32, device=noise_predictor.device)
    probab = noise_predictor(x_disc).flatten()
    z = model.encoder(x_disc)

# title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
# scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
# scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(x_disc, data['mask_x'], s=2, alpha=0.2, title=f'{data_name}: input').show()
scatter(x_disc, probab, s=2, alpha=0.2, title=f'{data_name}: probability', filename='hsphere_disc_prob.html').show()
scatter(x_disc, probab > 0.5, s=2, alpha=0.2, title=f'{data_name}: classification').show()

# if plot_recon:
#     title = f'[RECON] {title}'
#     if savefolder is not None:
#         filename = f"{savefolder}/{title1}.html"
#     # scatter(xh, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/utilities/parsing.py:269: UserWarning:

Attribute 'preprocessor' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['preprocessor'])`.



In [27]:
probab

tensor([0.5653, 0.5640, 0.5737,  ..., 0.5723, 0.5671, 0.5680])

In [28]:
func = lambda x: noise_predictor(x).reshape(-1,1)
jac = jacobian(func, x_disc).squeeze()

In [29]:
# jac_norm = jac / torch.sqrt(torch.square(jac).sum(axis=1)).reshape(-1,1)
jac_norm = jac

In [30]:
# fig = scatter(x_disc.detach().cpu().numpy(), probab, s=2, alpha=0.2)
fig = scatter(x_disc, probab > 0.5, s=2, alpha=0.2)
scale = 1
idx = np.random.choice(np.where(probab > 0.5)[0], 10)
for i in idx:
    x0 = x_disc.detach().cpu().numpy()[i,:]
    vector = jac[i,:].detach().cpu().numpy()
    normalized_vector = vector / np.sqrt((vector ** 2).sum())
    # Calculate the endpoint of the vector
    end_point = [x0[0] + normalized_vector[0] * scale,
                x0[1] + normalized_vector[1] * scale,
                x0[2] + normalized_vector[2] * scale]

    # Create the line part of the vector
    normal_vector_3d = go.Scatter3d(
        x=[x0[0], end_point[0]],
        y=[x0[1], end_point[1]],
        z=[x0[2], end_point[2]],
        mode='lines',
        line=dict(color='black', width=5)
    )

    # Create a cone at the end of the vector
    cone_marker = go.Cone(
        x=[end_point[0]],
        y=[end_point[1]],
        z=[end_point[2]],
        u=[normalized_vector[0]],
        v=[normalized_vector[1]],
        w=[normalized_vector[2]],
        sizemode='absolute',
        sizeref=0.3,  # Adjust this value to change the size of the cone
        showscale=False,
        colorscale=[[0, 'black'], [1, 'black']],  # Ensures the cone is green
        anchor='tail'  # Anchors the cone at the base, making it point away from the starting point
    )
    fig.add_trace(normal_vector_3d)
    fig.add_trace(cone_marker)

# fig.write_html('discriminator_gradient_on_mfd.html')
fig.show()

In [31]:
# fig = scatter(x_disc.detach().cpu().numpy(), probab, s=2, alpha=0.2)
fig = scatter(x_disc, probab < 0.5, s=2, alpha=0.2)
scale = 1
idx = np.random.choice(np.where(probab < 0.5)[0], 10)
for i in idx:
    x0 = x_disc.detach().cpu().numpy()[i,:]
    vector = jac[i,:].detach().cpu().numpy()
    normalized_vector = vector / np.sqrt((vector ** 2).sum())
    # Calculate the endpoint of the vector
    end_point = [x0[0] + normalized_vector[0] * scale,
                x0[1] + normalized_vector[1] * scale,
                x0[2] + normalized_vector[2] * scale]

    # Create the line part of the vector
    normal_vector_3d = go.Scatter3d(
        x=[x0[0], end_point[0]],
        y=[x0[1], end_point[1]],
        z=[x0[2], end_point[2]],
        mode='lines',
        line=dict(color='black', width=5)
    )

    # Create a cone at the end of the vector
    cone_marker = go.Cone(
        x=[end_point[0]],
        y=[end_point[1]],
        z=[end_point[2]],
        u=[normalized_vector[0]],
        v=[normalized_vector[1]],
        w=[normalized_vector[2]],
        sizemode='absolute',
        sizeref=0.3,  # Adjust this value to change the size of the cone
        showscale=False,
        colorscale=[[0, 'black'], [1, 'black']],  # Ensures the cone is green
        anchor='tail'  # Anchors the cone at the base, making it point away from the starting point
    )
    fig.add_trace(normal_vector_3d)
    fig.add_trace(cone_marker)

# fig.write_html('discriminator_gradient_off_mfd.html')
fig.show()

ValueError: 'a' cannot be empty unless no samples are taken

In [ ]:
# fig = scatter(x_disc.detach().cpu().numpy(), probab, s=2, alpha=0.2)
fig = scatter(x_disc, probab > 0.5, s=2, alpha=0.2)
scale = 1
idx = np.random.choice(np.where(probab > 0.5)[0], 10)
for i in idx:
    x0 = x_disc.detach().cpu().numpy()[i,:]
    vector = jac[i,:].detach().cpu().numpy()
    # normalized_vector = vector / np.sqrt((vector ** 2).sum())
    normalized_vector = vector
    # Calculate the endpoint of the vector
    end_point = [x0[0] + normalized_vector[0] * scale,
                x0[1] + normalized_vector[1] * scale,
                x0[2] + normalized_vector[2] * scale]

    # Create the line part of the vector
    normal_vector_3d = go.Scatter3d(
        x=[x0[0], end_point[0]],
        y=[x0[1], end_point[1]],
        z=[x0[2], end_point[2]],
        mode='lines',
        line=dict(color='black', width=5)
    )

    # Create a cone at the end of the vector
    cone_marker = go.Cone(
        x=[end_point[0]],
        y=[end_point[1]],
        z=[end_point[2]],
        u=[normalized_vector[0]],
        v=[normalized_vector[1]],
        w=[normalized_vector[2]],
        sizemode='absolute',
        sizeref=0.3,  # Adjust this value to change the size of the cone
        showscale=False,
        colorscale=[[0, 'black'], [1, 'black']],  # Ensures the cone is green
        anchor='tail'  # Anchors the cone at the base, making it point away from the starting point
    )
    fig.add_trace(normal_vector_3d)
    fig.add_trace(cone_marker)

fig.write_html('discriminator_gradient_on_mfd_no_norm.html')
fig.show()

In [ ]:
# fig = scatter(x_disc.detach().cpu().numpy(), probab, s=2, alpha=0.2)
fig = scatter(x_disc, probab > 0.5, s=2, alpha=0.2)
scale = 1
idx = np.random.choice(np.where(probab < 0.5)[0], 10)
for i in idx:
    x0 = x_disc.detach().cpu().numpy()[i,:]
    vector = jac[i,:].detach().cpu().numpy()
    normalized_vector = vector
    # normalized_vector = vector / np.sqrt((vector ** 2).sum())
    # Calculate the endpoint of the vector
    end_point = [x0[0] + normalized_vector[0] * scale,
                x0[1] + normalized_vector[1] * scale,
                x0[2] + normalized_vector[2] * scale]

    # Create the line part of the vector
    normal_vector_3d = go.Scatter3d(
        x=[x0[0], end_point[0]],
        y=[x0[1], end_point[1]],
        z=[x0[2], end_point[2]],
        mode='lines',
        line=dict(color='black', width=5)
    )

    # Create a cone at the end of the vector
    cone_marker = go.Cone(
        x=[end_point[0]],
        y=[end_point[1]],
        z=[end_point[2]],
        u=[normalized_vector[0]],
        v=[normalized_vector[1]],
        w=[normalized_vector[2]],
        sizemode='absolute',
        sizeref=0.3,  # Adjust this value to change the size of the cone
        showscale=False,
        colorscale=[[0, 'black'], [1, 'black']],  # Ensures the cone is green
        anchor='tail'  # Anchors the cone at the base, making it point away from the starting point
    )
    fig.add_trace(normal_vector_3d)
    fig.add_trace(cone_marker)

fig.write_html('discriminator_gradient_off_mfd_no_norm.html')
fig.show()

In [ ]:
# fig = scatter(x_disc.detach().cpu().numpy(), probab, s=2, alpha=0.2)
fig = scatter(x_disc, probab > 0.5, s=2, alpha=0.2)
scale = 1
idx = np.random.choice(np.where(probab > 0.5)[0], 10)
for i in idx:
    x0 = x_disc.detach().cpu().numpy()[i,:]
    # vector = jac[i,:].detach().cpu().numpy()
    # normalized_vector = vector / np.sqrt((vector ** 2).sum())
    normalized_vector = jac_norm[i,:].detach().cpu().numpy()
    # Calculate the endpoint of the vector
    end_point = [x0[0] + normalized_vector[0] * scale,
                x0[1] + normalized_vector[1] * scale,
                x0[2] + normalized_vector[2] * scale]

    # Create the line part of the vector
    normal_vector_3d = go.Scatter3d(
        x=[x0[0], end_point[0]],
        y=[x0[1], end_point[1]],
        z=[x0[2], end_point[2]],
        mode='lines',
        line=dict(color='black', width=5)
    )

    # Create a cone at the end of the vector
    cone_marker = go.Cone(
        x=[end_point[0]],
        y=[end_point[1]],
        z=[end_point[2]],
        u=[normalized_vector[0]],
        v=[normalized_vector[1]],
        w=[normalized_vector[2]],
        sizemode='absolute',
        sizeref=0.3,  # Adjust this value to change the size of the cone
        showscale=False,
        colorscale=[[0, 'black'], [1, 'black']],  # Ensures the cone is green
        anchor='tail'  # Anchors the cone at the base, making it point away from the starting point
    )
    fig.add_trace(normal_vector_3d)
    fig.add_trace(cone_marker)

fig.write_html('discriminator_gradient_on_mfd.html')
fig.show()

In [ ]:
vecs = torch.randn_like(jac_norm)

In [ ]:
(vecs * jac_norm).sum(axis=1)

tensor([ 0.4205, -0.2067,  1.1011,  ...,  1.6590,  1.8720, -0.9131],
       grad_fn=<SumBackward1>)